In [3]:
import numpy as np

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim 

import requests 
from pandas.io.json import json_normalize 


import matplotlib.cm as cm
import matplotlib.colors as colors


from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium

#!conda install -c conda-forge lxml --yes
import lxml

print('Libraries imported.')

Libraries imported.


### Read mta data into dataframe

In [19]:
# Read MTA data into dataframe
data =pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')
mta_data=data[0]

mta_data.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned                        NaN
1         M2A      Not assigned                        NaN
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

### Cleanup MTA data to remove **Not assigned** Boroughs from dataframe

In [20]:
index=mta_data[mta_data['Borough']=='Not assigned'].index
mta_data.drop(index,inplace=True)
mta_data.reset_index(drop=True, inplace=True)
mta_data.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

### Use the .shape method to print the number of rows in mta dataframe

In [21]:
print(mta_data.shape[0],"rows in the dataframe")

103 rows in the dataframe


### Read geographical coordinates of each postal code

In [22]:
geocodes=pd.read_csv('https://cocl.us/Geospatial_data')
geocodes.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

###  Add latitude and the longitude coordinates of each neighborhood

In [23]:
mta_data=pd.merge(mta_data, geocodes, on='Postal Code')
mta_data.head()

Postal Code           Borough                                 Neighborhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [1]:
# The code was removed by Watson Studio for sharing.

In [25]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [27]:
mta_data = getNearbyVenues(names=mta_data['Neighborhood'],
                                   latitudes=mta_data['Latitude'],
                                   longitudes=mta_data['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [30]:
mta_data.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

#### Size of the mta venue dataframe

In [31]:
print(mta_data.shape)
mta_data.head()

(2136, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

#### Number of venues for each neighborhood

In [32]:
mta_data.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                 11   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      23   
Berczy Park                                                            58   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           23   
Business reply mail Processing Centre, South Ce...                     17   
CN Tower, King and Spadina, Railway Lands, Harb...                     14   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  12   
Cedarbrae                                                               8   
Central Bay Street                                                     62   
Christie                                                               17   
Church and Wellesley                                                   77   
Clarks Corners, Tam O'Shanter, Sullivan                                13   
Cliffside, Cliffcrest, Scarborough Village West                         3   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             33   
Davisville North                                                        7   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              27   
Dorset Park, Wexford Heights, Scarborough Town ...                      6   
Downsview                                                              18   
Dufferin, Dovercourt Village                                           16   
East Toronto, Broadview North (Old East York)                           3   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      7   
Fairview, Henry Farm, Oriole                                           64   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                        10   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       5   
Humber Summit                                                           1   
Humberlea, Emery                                                        2   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         22   
Kennedy Park, Ionview, East Birchmount Park                             7   
Kensington Market, Chinatown, Grange Park                              58   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       13   
Lawrence Park                                                           3   
Leaside                                                                32   
Little Portugal, Trinity                                               44   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

#### unique categories from all the returned venues

In [33]:
print('There are {} uniques categories.'.format(len(mta_data['Venue Category'].unique())))

There are 271 uniques categories.


## Analyze Each Neighborhood

In [45]:
# one hot encoding
mta_onehot = pd.get_dummies(mta_data[['Venue Category']], prefix="", prefix_sep="")
mta_onehot.drop('Neighborhood',axis=1,inplace=True)
# add neighborhood column back to dataframe
mta_onehot['Neighborhood'] = mta_data['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [mta_onehot.columns[-1]] + list(mta_onehot.columns[:-1])
mta_onehot = mta_onehot[fixed_columns]

mta_onehot.head()

Neighborhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0               0                 0                   0      0   
1               0                 0                   0      0   
2               0                 0                   0      0   
3               0                 0                   0      0   
4               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0    

In [46]:
mta_onehot.shape

(2136, 271)

#### group rows by neighborhood and mean of the frequency of occurrence of each category

In [47]:
mta_grouped = mta_onehot.groupby('Neighborhood').mean().reset_index()
mta_grouped

Neighborhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   Business reply mail Processing Centre, South C...           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
10                                Caledonia-Fairbanks           0.000000   
11              Canada Post Gateway Processing Centre           0.000000   
12                                          Cedarbrae           0.000000   
13                                 Central Bay Street           0.000000   
14                                           Christie           0.000000   
15                               Church and Wellesley           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
18                     Commerce Court, Victoria Hotel           0.000000   
19                                         Davisville           0.000000   
20                                   Davisville North           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
22                                          Don Mills           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                          Downsview           0.000000   
25                       Dufferin, Dovercourt Village           0.000000   
26      East Toronto, Broadview North (Old East York)           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
28                       Fairview, Henry Farm, Oriole           0.000000   
29             First Canadian Place, Underground city           0.000000   
30    Forest Hill North & West, Forest Hill Road Park           0.000000   
31                           Garden District, Ryerson           0.000000   
32                                          Glencairn           0.000000   
33                    Golden Mile, Clairlea, Oakridge           0.000000   
34                  Guildwood, Morningside, West Hill           0.000000   
35  Harbourfront East, Union Station, Toronto Islands           0.000000   
36                      High Park, The Junction South           0.000000   
37                                  Hillcrest Village           0.000000   
38                                      Humber Summit           0.000000   
39                                   Humberlea, Emery           0.000000   
40                                 Humewood-Cedarvale           0.000000   
41                     India Bazaar, The Beaches West           0.000000   
42        Kennedy Park, Ionview, East Birchmount Park           0.000000   
43          Kensington Market, Chinatown, Grange Park           0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
45                   Lawrence Manor, Lawrence Heights           0.076923   
46                                      Lawrence Park           0.000000   
47                                            Leaside           0.000000   
48                           Little Portugal, Trinity           0.000000   
49                                     Malvern, Rouge           0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...           0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...           0.000000   
52           

In [48]:
mta_grouped.shape

(97, 271)

#### Print each neighborhood along with the top 5 most common venues

In [49]:
num_top_venues = 5

for hood in mta_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = mta_grouped[mta_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                       venue  freq
0               Skating Rink  0.25
1                     Lounge  0.25
2             Breakfast Spot  0.25
3  Latin American Restaurant  0.25
4          Accessories Store  0.00


----Alderwood, Long Branch----
                venue  freq
0         Pizza Place  0.18
1            Pharmacy  0.09
2  Athletics & Sports  0.09
3      Sandwich Place  0.09
4                 Gym  0.09


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0                       Bank  0.10
1                Coffee Shop  0.10
2  Middle Eastern Restaurant  0.05
3        Fried Chicken Joint  0.05
4           Sushi Restaurant  0.05


----Bayview Village----
                 venue  freq
0                 Café  0.25
1                 Bank  0.25
2  Japanese Restaurant  0.25
3   Chinese Restaurant  0.25
4    Accessories Store  0.00


----Bedford Park, Lawrence Manor East----
                venue  freq
0  Italian Restaurant  0.09
1  

#### New dataframe to display the top 10 venues for each neighborhood.

In [50]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [51]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = mta_grouped['Neighborhood']

for ind in np.arange(mta_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(mta_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village                  Café   
4                Bedford Park, Lawrence Manor East            Restaurant   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Latin American Restaurant        Breakfast Spot          Skating Rink   
1                        Gym          Dance Studio           Coffee Shop   
2                Coffee Shop         Shopping Mall        Sandwich Place   
3                       Bank    Chinese Restaurant   Japanese Restaurant   
4           Sushi Restaurant           Coffee Shop    Italian Restaurant   

  5th Most Common Venue      6th Most Common Venue 7th Most Common Venue  \
0               Dog Run               Dessert Shop    Dim Sum Restaurant   
1          Skating Rink                   Pharmacy                   Pub   
2           Supermarket  Middle Eastern Restaurant      Sushi Restaurant   
3         Deli / Bodega               Dessert Shop    Dim Sum Restaurant   
4        Sandwich Place                  Juice Bar                  Café   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                 Diner        Discount Store    Distribution Center  
1        Sandwich Place    Athletics & Sports                   Pool  
2            Restaurant         Deli / Bodega    Fried Chicken Joint  
3                 Diner        Discount Store    Distribution Center  
4               Butcher                   Pub           Liquor Store

## Cluster Neighborhoods

In [54]:
# set number of clusters
kclusters = 5

mta_grouped_clustering = mta_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mta_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [55]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

mta_merged = mta_data

mta_merged = mta_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

mta_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  Cluster Labels  1st Most Common Venue  \
0                   Park               0                   Park   
1      Food & Drink Shop               0                   Park   
2           Hockey Arena               1  Portuguese Restaurant   
3            Coffee Shop               1  Portuguese Restaurant   
4  Portuguese Restaurant               1  Portuguese Restaurant   

  2nd Most Common Venue 3rd Most Common Venue       4th Most Common Venue  \
0     Food & Drink Shop           Yoga Studio                     Dog Run   
1     Food & Drink Shop           Yoga Studio                     Dog Run   
2          Intersection           Coffee Shop  Financial or Legal Service   
3          Intersection           Coffee Shop  Financial or Legal Service   
4          Intersection           Coffee Shop  Financial or Legal Service   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0          Dessert Shop    Dim Sum Restaurant                 Diner   
1          Dessert Shop    Dim Sum Restaurant                 Diner   
2          Hockey Arena               Dog Run          Dessert Shop   
3          Hockey Arena               Dog Run          Dessert Shop   
4          Hockey Arena               Dog Run          Dessert Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0        Discount Store   Distribution Center       Doner Restaurant  
1        Discount Store   Distribution Center       Doner Restaurant  
2    Dim Sum Restaurant                 Diner         Discount Store  
3    Dim Sum Restaurant                 Diner         Discount Store  
4    Dim Sum Restaurant                 Diner         Discount Store

In [59]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="can_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [63]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(mta_merged['Venue Latitude'], mta_merged['Venue Longitude'], mta_merged['Neighborhood'], mta_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters